# Project: Investigate a Movies Dataset

## Table of Contents
<ul>
<li><a href="#intro">Introduction</a></li>
<li><a href="#wrangling">Data Wrangling</a></li>
<li><a href="#eda">Exploratory Data Analysis</a></li>
<li><a href="#conclusions">Conclusions</a></li>
</ul>

<a id='intro'></a>
## Introduction

This document presents the analysis carried out on the dataset: TMDb movie data
(cleaned from original data on Kaggle). It contains information about more than 10,000 movies obtained from The Movie Database (TMDb).

For this analisys, initially considered studying the popularity and revenue generated by the films. However, there are many records with unreported values for budget and income, so the possibility of studying income was discarded, as can be seen below in this document.

### Questions

<ul>This study aims to answer five questions:
<li> Which numerical variable most influences popularity?
<li> What are the most popular genres year on year?
<li>Which
    <ul>
    <li>actors, 
    <li>directors and 
    <li>production companies develop the most popular films?
    </ul>
</ul>

In [112]:
# Importing libraries to be used
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from scipy.stats import zscore

In this study, intensive use is made of box plot graphs. For that reason, a function called boxplot is created to avoid this repetitive code.

In [113]:
""" Function that draw a boxplot using plotly library, with all points graphed.
    Only accept up to two columns, for two dimensions of the graph
    IN:
        - df: Pandas Dataframe with data to be used for graph
        - columns: list with columns of the dataframe to be graphed
    OUT:
        Only in case of error, prints a message noticing
"""
def boxplot(df, columns):
    if len(columns) == 1:
        fig = go.Figure(px.box(df[columns[0]], y=columns[0]))
    elif len(columns) == 2:
        fig = go.Figure(px.box(df[[columns[0],columns[1]]], x=columns[0], y=columns[1]))
    else:
        print("Only one or two dimensions; no more, no less.")
        return
    fig.show()

    
""" Very similar to previous function, the difference is in the limit of y-axis

    IN:
        - df: Pandas Dataframe with data to be used for graph
        - columns: list with columns of the dataframe to be graphed
        - yrange: list with range to display for Y axis
    OUT:
        Only in case of error, prints a message noticing
"""
def boxplot_y_range(df, columns, y_range):
    if len(columns) == 1:
        fig = go.Figure(px.box(df[columns[0]], y=columns[0], points="all"))
    elif len(columns) == 2:
        fig = go.Figure(px.box(df[[columns[0],columns[1]]], x=columns[0], y=columns[1]))
    else:
        print("Only one or two dimensions; no more, no less.")
        return
    fig.update_yaxes(range=y_range)
    fig.show()

    
""" Function that draw a scatterplot using plotly library.
    Only accept two columns, for two dimensions of the graph
    IN:
        - df: Pandas Dataframe with data to be used for graph
        - columns: list with columns of the dataframe to be graphed
    OUT:
        Only in case of error, prints a message noticing
"""
def scatterplot(df, columns):
    if len(columns) == 2:
        fig = go.Figure(px.scatter(df, x=columns[0], y=columns[1], opacity=0.3,
            trendline='ols', trendline_color_override='darkblue'))
        fig.show()
    else:
        print("Only two dimensions; no more, no less.")
        return

""" Function that draw a bubbles graph using plotly library.
    Only accept two columns, for two dimensions of the graph
    IN:
        - df: Pandas Dataframe with data to be used for graph
        - columns: list with columns of the dataframe to be graphed
"""
def bubbles(df, columns):
    fig = px.scatter(df, x=columns[0], y=columns[1], size=columns[2], 
                     color=columns[3], hover_name=columns[4])
    fig.show()

<a id='wrangling'></a>
## Data Wrangling

The data for this analysis has been made available by Kaggle, in this code it is downloaded directly from its source for further cleaning, organisation and analysis.bold text

In [114]:
# Reading the data source
df = pd.read_csv('https://d17h27t6h515a5.cloudfront.net/topher/2017/October/59dd1c4c_tmdb-movies/tmdb-movies.csv')

### Budget and Revenue

These variables express monetary values of investment and return; there are two alternative versions that are adjusted in 2010 US dollars. In order to perform comparable analyses, the adjusted versions of these variables are used.

### Data Cleaning 

First of all, before performing any kind of treatment on the data it is necessary to look at it, to understand what we are working with. For this, Python language instructions are used to know the sample size and types of data.

In [115]:
# Before to clean data, is recommendable know the shape of the dataset
df.shape

(10866, 21)

In [116]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10866 entries, 0 to 10865
Data columns (total 21 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   id                    10866 non-null  int64  
 1   imdb_id               10856 non-null  object 
 2   popularity            10866 non-null  float64
 3   budget                10866 non-null  int64  
 4   revenue               10866 non-null  int64  
 5   original_title        10866 non-null  object 
 6   cast                  10790 non-null  object 
 7   homepage              2936 non-null   object 
 8   director              10822 non-null  object 
 9   tagline               8042 non-null   object 
 10  keywords              9373 non-null   object 
 11  overview              10862 non-null  object 
 12  runtime               10866 non-null  int64  
 13  genres                10843 non-null  object 
 14  production_companies  9836 non-null   object 
 15  release_date       

#### Search for duplicates

Duplicate tuples are searched for and one of them is left.

In [117]:
# Detecting duplicated tuples
sum(df.duplicated())

1

In [118]:
# Deleting duplicates
df.drop_duplicates(inplace=True)

#### Treatment of nulls

There are columns storing multiple values, these columns do not respect the basic principle of atomicity of data, so they are separated into different columns. But before, they are reviewed if there are too much null values.

In [119]:
df['cast'].isna().sum()

76

In [120]:
df['tagline'].isna().sum()

2824

In [121]:
df['director'].isna().sum()

44

In [122]:
df['keywords'].isna().sum()

1493

In [123]:
df['genres'].isna().sum()

23

In [124]:
df['production_companies'].isna().sum()

1030

In [125]:
df['homepage'].isna().sum()

7929

Due to the number of null data and/or because at this point they are not relevant for the analysis to be performed, the following has been considered to drop the following columns: keywords, tagline, homepage.

In [126]:
df = df.drop(columns=['keywords', 'tagline', 'homepage', 'overview'])

Because of the nature of this analysis, from concatenated fields, only the actors have been keeped at all. For director and genre, just the main is keeped.

In [127]:
# Separating concatenated categorical variables
df[['actor_1','actor_2','actor_3','actor_4','actor_5']] = df.cast.str.split('|', expand = True)
df[['genre']] = df.genres.str.split('|', expand = True)[0]
df[['director']] = df.director.str.split('|', expand = True)[0]
df[['production_company']] = df.production_companies.str.split('|', expand = True)[0]

In [128]:
# Eliminating possible white spaces or other undiserable characters
df[['actor_1']] = df['actor_1'].str.strip()
df[['actor_2']] = df['actor_2'].str.strip()
df[['actor_3']] = df['actor_3'].str.strip()
df[['actor_4']] = df['actor_4'].str.strip()
df[['actor_5']] = df['actor_5'].str.strip()
df[['genre']] = df['genre'].str.strip()
df[['director']] = df['director'].str.strip()
df[['production_company']] = df['production_company'].str.strip()
df[['imdb_id']] = df['imdb_id'].str.strip()

In [129]:
# Columns that have been split are eliminated, leaving columns derived from them
df = df.drop(columns=['cast', 'genres', 'production_companies'])

In [130]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10865 entries, 0 to 10865
Data columns (total 21 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id                  10865 non-null  int64  
 1   imdb_id             10855 non-null  object 
 2   popularity          10865 non-null  float64
 3   budget              10865 non-null  int64  
 4   revenue             10865 non-null  int64  
 5   original_title      10865 non-null  object 
 6   director            10821 non-null  object 
 7   runtime             10865 non-null  int64  
 8   release_date        10865 non-null  object 
 9   vote_count          10865 non-null  int64  
 10  vote_average        10865 non-null  float64
 11  release_year        10865 non-null  int64  
 12  budget_adj          10865 non-null  float64
 13  revenue_adj         10865 non-null  float64
 14  actor_1             10789 non-null  object 
 15  actor_2             10645 non-null  object 
 16  acto

A large amount of null data is observed in several of the columns of the dataset. At some point, the use of 'dropna' was considered to eliminate the rows with null records; finally it was decided to complete those records with the value "Uninformed", in order not to lose the rest of the information in those rows.

In the case of the actors, it was only applied for actor_1, understanding that there is a possibility that a film has few actors, and for this reason there is no actor 5, 4, 3 or 2; given this possibility, it was decided not to alter this information.

In [131]:
df['imdb_id'].fillna("Uninformed", inplace = True)
df['director'].fillna("Uninformed", inplace = True)
df['actor_1'].fillna("Uninformed", inplace = True)
df['genre'].fillna("Uninformed", inplace = True)
df['production_company'].fillna("Uninformed", inplace = True)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10865 entries, 0 to 10865
Data columns (total 21 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id                  10865 non-null  int64  
 1   imdb_id             10865 non-null  object 
 2   popularity          10865 non-null  float64
 3   budget              10865 non-null  int64  
 4   revenue             10865 non-null  int64  
 5   original_title      10865 non-null  object 
 6   director            10865 non-null  object 
 7   runtime             10865 non-null  int64  
 8   release_date        10865 non-null  object 
 9   vote_count          10865 non-null  int64  
 10  vote_average        10865 non-null  float64
 11  release_year        10865 non-null  int64  
 12  budget_adj          10865 non-null  float64
 13  revenue_adj         10865 non-null  float64
 14  actor_1             10865 non-null  object 
 15  actor_2             10645 non-null  object 
 16  acto

As mentioned above, the adjusted values for budget and return are considered during this analysis, so their unadjusted values are removed from the dataset.

In [132]:
df = df.drop(columns=['budget', 'revenue'])

#### Data type correction
Dates come in string format instead of the appropriate data type; on the other hand, years come with two digits. When converted to Python date format some of the years are not interpreted correctly; for example the year 70 is interpreted as 2070 instead of 1970. Fortunately, there is the release_year column which helps in a correct interpretation of the date.

In [133]:
df['release_date']

0          6/9/15
1         5/13/15
2         3/18/15
3        12/15/15
4          4/1/15
           ...   
10861     6/15/66
10862    12/21/66
10863      1/1/66
10864     11/2/66
10865    11/15/66
Name: release_date, Length: 10865, dtype: object

In [134]:
# It separates the day and month fields, and joins them with the correct year.
month = df['release_date'].str.split('/').str[0]
day = df['release_date'].str.split('/').str[1]

In [135]:
# It concatenates month, day and year of release.
release_date = month.str.cat(day, '/')
release_date = release_date.str.cat(pd.Series(df['release_year'], dtype="string"), '/')

In [136]:
# After, the release_date column is replaced by a correctly formed one.
df = df.drop(columns = ['release_date'])
df['release_date'] = release_date

In [137]:
# Finally, it corrects data type
df['release_date'] = pd.to_datetime(df['release_date'])

In [138]:
df[['release_date']].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10865 entries, 0 to 10865
Data columns (total 1 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   release_date  10865 non-null  datetime64[ns]
dtypes: datetime64[ns](1)
memory usage: 169.8 KB


At this point, in the categorical variables there is no data that needs to be cleaned, so the numerical variables will be looked at one by one.

##### Popularity

Popularity reaches extreme values between 0 and 32.99. However, box-plot graph shows:


*   Bottom fence with values near to zero
*   Upper fence of 1.47
*   Median is 0.38
*   Quartil 1 is 0.20
*   Quartil 3 is 0.71

This, shows a wide quantity of data in the category of outlier.

In [139]:
boxplot(df, ['popularity'])

In [140]:
df['popularity'].describe()

count    10865.000000
mean         0.646446
std          1.000231
min          0.000065
25%          0.207575
50%          0.383831
75%          0.713857
max         32.985763
Name: popularity, dtype: float64

In order to reduce outliers, the technique of measuring distance from the mean, in standard deviations, is applied through the use of z-scores. In this study, points more than three standard deviations away will be eliminated.

In [141]:
# Definition of z-scores, they are stored in the dataframe 'zscores'.
zscores = df[['popularity']].apply(zscore)
zscores

popularity
0       32.333342
1       27.768358
2       12.463758
3       10.524713
4        8.686963
...           ...
10861   -0.565743
10862   -0.580795
10863   -0.581197
10864   -0.582021
10865   -0.610414

[10865 rows x 1 columns]

In [142]:
# The 'is_outlier' dataframe stores the results of logic tests that evaluate whether the Z-value
# is within the defined limits (boolean values). These results are then concatenated with the main dataframe;
# finally, the boolean value is used to decide which rows are kept and which are removed.
is_outlier = (zscores['popularity'] > 3) | (zscores['popularity'] < -3)
df['is_outlier'] = is_outlier
df = df[df['is_outlier'] != True]
df = df.drop(columns = ['is_outlier'])
df.shape

(10696, 19)

It is observed that there are still outliers in the new data distribution, so the process is repeated, only for a second time.

In [143]:
boxplot(df, ['popularity'])

In [144]:
df['popularity'].describe()

count    10696.000000
mean         0.560135
std          0.568983
min          0.000065
25%          0.205178
50%          0.378082
75%          0.689131
max          3.644541
Name: popularity, dtype: float64

In [145]:
zscores = df[['popularity']].apply(zscore)
zscores

popularity
34       5.421165
35       5.268789
36       4.918103
37       4.884382
38       4.705519
...           ...
10861   -0.842836
10862   -0.869296
10863   -0.870003
10864   -0.871451
10865   -0.921364

[10696 rows x 1 columns]

In [146]:
is_outlier = (zscores['popularity'] > 3) | (zscores['popularity'] < -3)
df['is_outlier'] = is_outlier
df = df[df['is_outlier'] != True]
df = df.drop(columns = ['is_outlier'])
df.shape

(10421, 19)

##### Revenue_adj
Revenue reaches extreme values between 0 and US$1.58 billions. However, its description shows:

*   Median is 0
*   Quartil 1 is 0
*   Quartil 3 is 23.2 millions

These values can be explained by the fact that there are 6009 zero-valued tuples in revenue_adj. This may be due to unreported values from the source of the data. This assumption is made due to the fact that several of the films reported with zero revenue are first-rate and well-known films, such as: "The Lion King", "Batman: The Dark Knight Returns, Part 1", "Once Upon a Time in America", among others.

In this case, given the number of zero entries, the decision is not to consider this column in the analysis; as mencioned <a href="#intro">in the introductory section</a>.


In [147]:
df['revenue_adj'].describe()

count    1.042100e+04
mean     3.584879e+07
std      9.551453e+07
min      0.000000e+00
25%      0.000000e+00
50%      0.000000e+00
75%      2.448665e+07
max      2.167325e+09
Name: revenue_adj, dtype: float64

In [148]:
df[df.revenue_adj == 0].count()['revenue_adj']

6009

##### Budget_adj
A similar to revenue_adj situation has been reached in budget_adj, with 5689 zero-values. For this reason, it is not considered in the analysis.


In [149]:
df['budget_adj'].describe()

count    1.042100e+04
mean     1.466656e+07
std      2.889181e+07
min      0.000000e+00
25%      0.000000e+00
50%      0.000000e+00
75%      1.728535e+07
max      4.250000e+08
Name: budget_adj, dtype: float64

In [150]:
df[df.budget_adj == 0].count()['budget_adj']

5689

In [151]:
df = df.drop(columns = ['budget_adj', 'revenue_adj'])
df.shape

(10421, 17)

##### Runtime
Variable that reports the duration of the films.

In [152]:
boxplot(df, ['runtime'])

In [153]:
df.runtime.describe()

count    10421.000000
mean       101.322234
std         31.481625
min          0.000000
25%         90.000000
50%         98.000000
75%        110.000000
max        900.000000
Name: runtime, dtype: float64

In [154]:
df[df.runtime == 0].count()['runtime']

31

In this case, it has been determined not to eliminate outliers. The reason for this is due to the context of this variable, as it indicates the duration of the film, eliminating outliers would leave out short or feature films that are icons of cinema, which for this case may be of interest to analyse.

A special case exist on runtime with zero-values, so these cases are imputed by the mean of that column.

In [155]:
# Changing zero values by None, in order to use 'fillna' for imputation using mean.
df.loc[df['runtime'] == 0, 'runtime'] = None
df['runtime'].fillna(df['runtime'].mean(), inplace = True)
df.runtime.describe()

count    10421.000000
mean       101.624543
std         30.991275
min          2.000000
25%         90.000000
50%         98.000000
75%        110.000000
max        900.000000
Name: runtime, dtype: float64

##### Release_date
Variable that reports the date of the release of the films.

In [156]:
df.release_date.describe(datetime_is_numeric=True)

count                            10421
mean     2001-08-28 01:30:30.572881536
min                1960-01-01 00:00:00
25%                1994-11-23 00:00:00
50%                2005-12-07 00:00:00
75%                2011-09-01 00:00:00
max                2015-12-31 00:00:00
Name: release_date, dtype: object

##### Vote Count
Variable indicating the number of votes in the database.

In [157]:
boxplot(df, ['vote_count'])

In this case, outliers are detected and the criterion of eliminating values exceeding three times the standard deviation above the mean and below the mean, although this time it is applied directly without resorting to Z-scores.

In [158]:
df = df[(df['vote_count'] >= df['vote_count'].mean()-3*df['vote_count'].std()) & (df['vote_count'] <= df['vote_count'].mean()+3*df['vote_count'].std())]
df.shape

(10178, 17)

In [159]:
boxplot(df, ['vote_count'])

It is observed that outliers are still present in the new data distribution, so the process is repeated, only for a second time.

In [160]:
df = df[(df['vote_count'] >= df['vote_count'].mean()-3*df['vote_count'].std()) & (df['vote_count'] <= df['vote_count'].mean()+3*df['vote_count'].std())]
df.shape

(9850, 17)

##### Vote Average

This variable indicates the average number of votes that each of the films has received from the users. It mantains the criterion to consider outliers the values out of three standard deviations above the mean and below the mean.

In [161]:
boxplot(df, ['vote_average'])

In [162]:
df = df[(df['vote_average'] >= df['vote_average'].mean()-3*df['vote_average'].std()) & (df['vote_average'] <= df['vote_average'].mean()+3*df['vote_average'].std())]
boxplot(df, ['vote_average'])

<a id='eda'></a>
## Exploratory Data Analysis
Has been defined as dependent, the variable 'popularity'.

###### Analysing comparatively with some cuantitative variables
In first place, is important to know the data; for that reason, next, numerical variables are described. After that, possible relationships between numerical variables and the dependent variable, are studied.

In [163]:
df.describe()

id   popularity      runtime   vote_count  vote_average  \
count    9780.000000  9780.000000  9780.000000  9780.000000   9780.000000   
mean    66393.402249     0.443318   100.972839    81.576074      5.926605   
std     92849.746488     0.355506    30.454679   110.766363      0.891523   
min         5.000000     0.000065     2.000000    10.000000      3.200000   
25%     10956.750000     0.194934    90.000000    16.000000      5.300000   
50%     20760.500000     0.346767    98.000000    32.000000      6.000000   
75%     73572.250000     0.586087   110.000000    92.000000      6.500000   
max    417859.000000     2.227230   877.000000   576.000000      8.600000   

       release_year  
count   9780.000000  
mean    2000.837321  
std       13.007365  
min     1960.000000  
25%     1994.000000  
50%     2005.000000  
75%     2011.000000  
max     2015.000000

*Popularity vs Runtime*

Both, the data visualisation and the linear relationship projection show no major influence of the runtime variable on popularity.

In [164]:
scatterplot(df, ['runtime', 'popularity'])

*Popularity vs Vote Average*

The linear regression equation shows a low, almost horizontal slope. On the other hand, its low $r^2$ value 0.000344 indicates low representativeness of this projection.

In [165]:
scatterplot(df, ['vote_average', 'popularity'])

*Popularity vs Vote Count*

The linear regression equation shows a more tilted one, indicating a positive relationship. Furthermore, its $r^2$ value of 0.53 indicates a much more representative regression than the previous ones.

In [166]:
scatterplot(df, ['vote_count', 'popularity'])

###### Analysing comparatively with some cualitative variables

*Popularity vs Genre*

At a glance, there is no clear predominance of any one genre over the others, although they reach higher levels: Adventure, Animation, Family and Thriller. However, in the opposite direction, Documentary and Foreign are the least popular genres.

For this graph, the display is limited to the y-axis, in order to focus attention on the interquartile ranges.

In [167]:
boxplot_y_range(df, ['genre','popularity'], [0,1])

Next, the top ten of popularity based on mean:

In [168]:
popular_genres = df[['genre','popularity']].groupby(['genre']).mean().sort_values(by=['popularity'], ascending=False).head(10)
popular_genres

popularity
genre                      
Adventure          0.588340
Animation          0.547971
Fantasy            0.510408
Thriller           0.500299
Family             0.486493
Action             0.486251
Crime              0.478637
Science Fiction    0.471017
Romance            0.468101
Western            0.459089

*Popularity vs release_year*

In general terms, a concentration of extremely popular values is observed in the last years, however these are cases that could be considered as outliers of each year. The focus is on the interquartile range and the median of each year; this increases slightly over the years; being 1995 the year with the most high level of popularity and 1964 with the low level of popularity. Although it is not possible affirm than exists a causal relationship of the year of release of a film with respect to its popularity.

In [169]:
boxplot(df, ['release_year','popularity'])

*Popularity vs director*

Due to the large number of directors, it has been decided to limit the directors to those with at least 15 films registered in the dataset. Moreover, it allows us to analyse directors with a track record, avoiding the bias that could be avoided by a director with only one film. For example, if you take a director with only one film, superior to the others in popularity, graphically he would appear as a director far superior to the others; however, his success would be due to only one film.

In [170]:
# A new dataset is generated with the directors and the film count for each of them.
# Those with fifteen or more registered films are selected. Then, records with director 'Uninformed'
# are removed from this analysis.
dir_more_films = df[['director', 'id']].groupby(['director']).count()
dir_more_films = dir_more_films.rename(columns={'id': 'film_count'})
dir_more_films = dir_more_films[dir_more_films.film_count >= 15]
dir_more_films = dir_more_films.reset_index()
dir_more_films = dir_more_films[dir_more_films.director != 'Uninformed']

In [171]:
# The newly created dataset is used as a filter of the main dataset, so as to leave only 
# the data of directors with 15 or more films.
merged = pd.merge(dir_more_films, df, on=['director','director'], how='left')

In [172]:
boxplot_y_range(merged, ['director','popularity'], [0,1.6])

In this graph it is possible to note that there are some outstanding directors in terms of popularity. Such is the case of directors Ron Howard, Oliver Stone, Roman Polanski and John Carpenter.

*Popularity vs Actor*

Similar to the analysis of directors, with actors, a prior selection is made on the basis of the number of films in which they have participated.

As the actors were previously divided into five columns, there was the possibility of analysing only those who came first, discarding the others. However, it was decided to merge them all into a single dataset, filtering out those appearing in at least 25 films.

In [173]:
# A new dataset is generated with the actors and the film count for each of them.
# Those with fifteen or more registered films are selected. Then, records with actor 'Uninformed'
# are removed from this analysis.
actor_1 = df[['actor_1', 'id']].groupby(['actor_1']).count()
actor_1 = actor_1.rename(columns={'id': 'film_count'})
actor_2 = df[['actor_2', 'id']].groupby(['actor_2']).count()
actor_2 = actor_2.rename(columns={'id': 'film_count'})
actor_3 = df[['actor_3', 'id']].groupby(['actor_3']).count()
actor_3 = actor_3.rename(columns={'id': 'film_count'})
actor_4 = df[['actor_4', 'id']].groupby(['actor_4']).count()
actor_4 = actor_4.rename(columns={'id': 'film_count'})
actor_5 = df[['actor_5', 'id']].groupby(['actor_5']).count()
actor_5 = actor_5.rename(columns={'id': 'film_count'})

In [174]:
# Concatenating dataframes with actors
frames = [actor_1, actor_2, actor_3, actor_4, actor_5]
actors = pd.concat(frames)
actors = actors.reset_index()

In [175]:
# Grouping, filtering uninformed actors and those appearing in less than 30 films.
actors = actors.rename({'index': 'actor'}, axis='columns')
actors = actors.groupby(['actor']).sum()
actors = actors.reset_index()
actors = actors[actors.actor != 'Uninformed']
actors = actors[actors.film_count >= 30]
actors.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 63 entries, 285 to 18240
Data columns (total 2 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   actor       63 non-null     object
 1   film_count  63 non-null     int64 
dtypes: int64(1), object(1)
memory usage: 1.5+ KB


In [176]:
# The newly created dataset is used as a filter of the main dataset.
merged_1 = actors.merge(df, left_on='actor', right_on='actor_1', how='left', indicator=True)
merged_2 = actors.merge(df, left_on='actor', right_on='actor_2', how='left', indicator=True)
merged_3 = actors.merge(df, left_on='actor', right_on='actor_3', how='left', indicator=True)
merged_4 = actors.merge(df, left_on='actor', right_on='actor_4', how='left', indicator=True)
merged_5 = actors.merge(df, left_on='actor', right_on='actor_5', how='left', indicator=True)

In [177]:
# Concatenating datasets
frames = [merged_1, merged_2, merged_3, merged_4, merged_5]
merged = pd.concat(frames)

In [178]:
boxplot(merged, ['actor','popularity'])

It is observed that there are actors who achieve high levels of popularity for their films. It is important to remember that the actors analysed here are established actors, with at least 30 films in the dataset.

The most popular of all is Sylvester Stallone, followed closely by Nicole Kidman, Julia Roberts and Keanu Reeves. Jean-Claude Van Damme's regularity in film popularity is striking; while his films are not in the Top 5 of this select group of actors, the dispersion of his films' popularity is quite low.

In [179]:
company_more_films = df[['production_company', 'id']].groupby(['production_company']).count()
company_more_films = company_more_films.rename(columns={'id': 'film_count'})
company_more_films = company_more_films[company_more_films.film_count >= 30]
company_more_films = company_more_films.reset_index()
company_more_films = company_more_films[company_more_films.production_company != 'Uninformed']

In [180]:
merged = pd.merge(company_more_films, df, on=['production_company','production_company'], how='left')

In [181]:
boxplot(merged, ['production_company','popularity'])

Analysing these production companies, remembering that we have filtered out those with at least thirty films in our dataset, we can observe a predominance of some of them over the rest. This is the case with Dreamworks, Village Roadshow Pictures y Regency Enterprises. 

##### Most popular genres over the years

We work with the genres with the highest number of records, so that the graph is legible and each annotation in the graph is representative.

In [182]:
# The genres are grouped and counted and then filtered, and finally the uninformed records are eliminated.
popular_genres = df[['genre','id']].groupby(['genre']).count()
popular_genres = popular_genres.rename(columns={'id': 'film_count'})
popular_genres = popular_genres[popular_genres.film_count >= 200]
popular_genres = popular_genres.reset_index()
popular_genres = popular_genres[popular_genres.genre != 'Uninformed']
popular_genres

genre  film_count
0       Action        1341
1    Adventure         440
2    Animation         346
3       Comedy        2177
4        Crime         333
5  Documentary         429
6        Drama        2284
7      Fantasy         222
8       Horror         858
9     Thriller         440

In [183]:
# Application of 'Left Join' to filter the records of the main dataset and leave only
# those belonging to the previously selected genres.
merged = pd.merge(popular_genres, df, on=['genre','genre'], how='left')

The median is then calculated for each genre in each year.

In [184]:
popular_genres_by_year = merged[['genre','popularity','release_year']].groupby(['release_year', 'genre']).median().reset_index()

In this way it is possible to bring it to a graph where it is possible to observe the most popular genres each year. The decision to narrow down to the most popular genres, was made in order to improve the readability of the graph.<a id='genres_by_year'></a>

In [185]:
bubbles(popular_genres_by_year, ['release_year', 'popularity', 'popularity', 'genre','genre'])

Genres are noticeably more popular than the rest in some years. Such is the case of Animation, which escapes in 1962, and although in subsequent years it does not achieve the same level, it is always among the most outstanding bubbles. 

One genre that is consistently at the top of the bubble is Adventure.

Fantasy and Crime are other important genres in this visual analysis.

On the other hand, Documentaries are the genre that consistently ranks lowest in popularity among the selected genres.

<a id='conclusions'></a>
## Conclusions

In general, a number of relationships between variables could be observed. However, the quality of the data does not allow us to explore this issue further. In this sense, the following limitations are specified.

### Limitations of the study

The wide quantity of zero-values for budget and revenue, explained above, creates a major constraint for the study. Would be interesting analise the relationship between budget and revenue, or budget and popularity; for example. With the limitation mentioned, this is not possible.

### Final conclusions

For the study of this dataset, the following questions were posed and here are its answers:
<ul>
<li> Which numerical variable most influences popularity?
    <br><b>R1:</b> Analysing the numerical variables, Vote_Count has the strongest relationship with popularity. This can be seen visually in the scatter plot displayed previously, as well as in the linear regression line; both in the slope of the slope and in its $r^2$ value de 0.53.
    Although it is important to note that these results are in the context of the exercise. Given the nature of the variables being analysed, it is popularity that determines the number of votes in the database.
<li> What are the most popular genres year on year?
    <br><b>R2:</b> Animation, Adventure, Fantasy and Crime are the most important genres in terms of popularity (<a href="#genres_by_year">details here</a>).
<li>Which
    <ul>
    <li>actors, 
    <li>directors and 
    <li>production companies develop the most popular films?
    </ul>
    <br><b>R3:</b> The most popular of all actors is Sylvester Stallone, followed closely by Nicole Kidman, Julia Roberts and Keanu Reeves
    <br><b>R4:</b> In terms of directors, Ron Howard, Oliver Stone, Roman Polanski and John Carpenter; they are the ones who make the most popular films.
    <br><b>R5:</b> Production companies that develop most popular films are: Dreamworks, Village Roadshow Pictures y Regency Enterprises. 
</ul>


The data chosen for the study do allow descriptive statistics to be performed for each variable, allowing newly acquired knowledge in Python to be exercised.